## Setup a PostgreSQL database with the RDKit cartridge

In [1]:
# common usage
import pandas as pd # dataframes
# postgresql
import psycopg2 # query postgresql database
# chemoinformatics
from rdkit import rdBase
from rdkit import Chem # main RDKit module

In [2]:
# establish connection to the database
conn = psycopg2.connect(dbname="chembl_24_dev",user="gally")
cur = conn.cursor()

In [3]:
# print versions
print("Versions:\n")
print("RDKit: {}".format(rdBase.rdkitVersion))
# for postgresql we need to setup a cursor first
cur.execute('SELECT version()')
db_version = cur.fetchone()
print(db_version[0])

Versions:

RDKit: 2018.09.1
PostgreSQL 10.5 on x86_64-pc-linux-gnu, compiled by x86_64-conda_cos6-linux-gnu-cc (crosstool-NG fa8859cb) 7.2.0, 64-bit


In [4]:
# I copied/pasted the below commands from https://www.rdkit.org/docs/Cartridge.html
# chembl_24_dev is a subset from the chembl_24 posgresql database
# I replaced rdk.mols by rdk2.mols for this example
sql="""
create extension if not exists rdkit;
create schema rdk2;
select * into rdk2.mols from (select molregno,mol_from_ctab(molfile::cstring) m  from compound_structures) tmp where m is not null;
create index molidx on rdk2.mols using gist(m);
alter table rdk2.mols add primary key (molregno);
select molregno,torsionbv_fp(m) as torsionbv,morganbv_fp(m) as mfp2,featmorganbv_fp(m) as ffp2 into rdk2.fps from rdk2.mols;
create index fps_ttbv_idx on rdk2.fps using gist(torsionbv);
create index fps_mfp2_idx on rdk2.fps using gist(mfp2);
create index fps_ffp2_idx on rdk2.fps using gist(ffp2);
alter table rdk2.fps add primary key (molregno);
create or replace function get_mfp2_neighbors(smiles text)
returns table(molregno bigint, m mol, similarity double precision) as
$$
select molregno,m,tanimoto_sml(morganbv_fp(mol_from_smiles($1::cstring)),mfp2) as similarity
from rdk2.fps join rdk2.mols using (molregno)
where morganbv_fp(mol_from_smiles($1::cstring))%mfp2
order by morganbv_fp(mol_from_smiles($1::cstring))<%>mfp2;
$$ language sql stable ;
"""
cur.execute(sql)
conn.commit()

In [5]:
cur.execute("SELECT * FROM rdk2.mols WHERE m@>'c1ccccc1' LIMIT 10;")
res = cur.fetchall()
df = pd.DataFrame(res)
df.columns = [ c[0] for c in cur.description ] # get column index
df

molregno                                                  m
0    194848                CC(C)(C)c1cc(C(N)=O)cc(C(C)(C)C)c1O
1   1879935           CN(Cc1nnc2n1CCC2)S(=O)(=O)c1ccc(Br)cc1Cl
2    243213  O=C1N(Cc2ccc3ccccc3c2)[C@H]([C@@H](F)Cc2ccccc2...
3   2069682  COc1cc(/C=C(/C(=O)N2CCC=CC2=O)c2ccc(F)cc2)cc(O...
4    772447  CCS(=O)(=O)N1CCN(c2cc3c(cc2[N+](=O)[O-])n(C)c(...
5    215640                  CCCCn1c(=O)c2ncn(C)c2c2cc(C)ccc21
6   1786279  N#CC1=C(N)N(c2cccnc2)C2=C(C(=O)CCC2)C1c1cc2cc(...
7    137566        CC(C)(C)c1cc(NC(=O)NC2CCCCC2)n(-c2ccccc2)n1
8    813327  O=C(CCCn1c(=O)[nH]c2ccccc2c1=O)N1CCN(Cc2ccc3c(...
9    729364                  NC(=O)Cc1ccc(C(=O)c2ccc(Cl)cc2)s1

In [6]:
type(df.iloc[0]['m'])

str